In [2]:
import gradio as gr
import random
import openai
import os
from dotenv import load_dotenv, find_dotenv

_ = load_dotenv(find_dotenv())

openai.api_key  = os.getenv('OPENAI_API_KEY')

In [3]:
class Conversation:
    def __init__(self, prompt, num_of_round):
        self.prompt = prompt
        self.num_of_round = num_of_round
        self.messages = []
        self.messages.append({"role": "system", "content": self.prompt})

    def ask(self, question):
        try:
            self.messages.append( {"role": "user", "content": question})
            response = openai.ChatCompletion.create(
                model="gpt-3.5-turbo",
                messages=self.messages,
                temperature=0.5,
                max_tokens=300,
                top_p=1,
            )
        except Exception as e:
            print(e)
            return e

        message = response["choices"][0]["message"]["content"]
        self.messages.append({"role": "assistant", "content": message})
        
        if len(self.messages) > self.num_of_round*2 + 1:
            del self.messages[1:3]
        return message

In [4]:
with open('chatbot_03_prompt.md', 'r') as file:
    prompt = file.read()

prompt = '"""\n' + prompt + '\n"""'

conv = Conversation(prompt, 5)

def respond(message, chat_history):
    # bot_message = random.choice(["How are you?", "I love you", "I'm very hungry"])
    bot_message = conv.ask(message)
    chat_history.append((message, bot_message))
    return "", chat_history

    
init_conversation = [(None, "欢迎来到我们的 Chatbot! 请问有什么可以帮助你的吗?")]

with gr.Blocks(css="#chatbot{height:900px} .overflow-y-auto{height:1200px}") as demo:
    chatbot = gr.Chatbot(elem_id="chatbot", value=init_conversation, height="900px")
    msg = gr.Textbox()
    msg.submit(respond, [msg, chatbot], [msg, chatbot])

demo.launch()

Running on local URL:  http://127.0.0.1:7860

To create a public link, set `share=True` in `launch()`.
